## Backpropagation-based methods

In [ ]:
import torch
import torch.nn as nn
from torchvision import models

from torchvision import transforms
from PIL import Image

import matplotlib.pyplot as plt

# Part I: Vanilla backpropagation

**Question 1:** Given the following ResNet model and input image, compute the gradient of the top-1 output logit of the model with respect to the input image, following the Question 6. (Part I) of Practical Session 4.

In [ ]:
# Load a pre-trained resnet model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# use device = xla.device() if you want to use tpu.
model = models.resnet18(pretrained=True).to(device)
# Set the model to evaluation mode
model.eval()

img_path = 'dog_tp4.jpg'
input_image = Image.open(img_path)

# preprocessing for ResNet
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# set the ReLus to inplace = False
for i, (name, layer) in enumerate(model.named_modules()):
  if isinstance(layer, nn.ReLU):
    if name == "relu":
      getattr(model, name).inplace = False
    else:
      block, num, module = name.split(".")
      getattr(getattr(model,block)[int(num)], 'relu').inplace = False


# preprocess the image
input_tensor = preprocess(input_image)
# create a mini-batch as expected by the model
input_batch = input_tensor.unsqueeze(0)

################################################################################

**Question 2:** Perform Min-Max feature scaling on the RGB gradient from the previous step using `X_scaled = (X - X.min() ) / ( X.max() - X.min())`

**Question 3:** Visualize the scaled gradient using `plt.imshow()`.

# Part II: Deconvolution backpropagation

The goal of this section is to implement a variant of backpropagation known as deconvolution backpropagation. This approach focuses on modifying the gradient computation specifically for the ReLU activation function, rather than reimplementing the entire backpropagation algorithm from scratch. For additional details, please refer to lecture slide 230.

In [ ]:
# Load a pre-trained resnet model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# use device = xla.device() if you want to use tpu.
model = models.resnet18(pretrained=True).to(device)
# Set the model to evaluation mode
model.eval()

img_path = 'dog_tp4.jpg'
input_image = Image.open(img_path)

# preprocessing for ResNet
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# set the ReLus to inplace = False
for i, (name, layer) in enumerate(model.named_modules()):
  if isinstance(layer, nn.ReLU):
    if name == "relu":
      getattr(model, name).inplace = False
    else:
      block, num, module = name.split(".")
      getattr(getattr(model,block)[int(num)], 'relu').inplace = False


# preprocess the image
input_tensor = preprocess(input_image)
# create a mini-batch as expected by the model
input_batch = input_tensor.unsqueeze(0)

################################################################################

**Question 1:** Understand the provided code, which modifies the backpropagation process through ReLU.

In [ ]:
class reluDeconv(torch.autograd.Function):
    """
    We can implement our own custom autograd Functions by subclassing
    torch.autograd.Function and implementing the forward and backward passes
    which operate on Tensors.
    """
    def __init__(self, inplace=False):
      super(reluDeconv, self).__init__()
      self.inplace = inplace

    @staticmethod
    def forward(ctx, input):
        """
        In the forward pass we receive a Tensor containing the input and return
        a Tensor containing the output. ctx is a context object that can be used
        to stash information for backward computation. You can cache arbitrary
        objects for use in the backward pass using the ctx.save_for_backward method.
        """
        # ctx.save_for_backward(input)
        output = ???
        return output

    @staticmethod
    def backward(ctx, grad_output):
        """
        In the backward pass we receive a Tensor containing the gradient of the loss
        with respect to the output, and we need to compute the gradient of the loss
        with respect to the input.
        """
        grad_input = ???
        return grad_input


# what does this part do?
class reluDeconvWrapper(nn.Module):
    def __init__(self):
        super(reluDeconvWrapper, self).__init__()
    def forward(self, input):
        return reluDeconv.apply(input)

def replace_relu(model):
    for name, module in model.named_children():
        if isinstance(module, nn.ReLU):
            setattr(model, name, reluDeconvWrapper())
        else:
            replace_relu(module)

replace_relu(model)

**Question 2:** Complete the previous code to implement deconvolution-backpropagation as described in the lecture slide 230.
(Hint: Pay close attention to the tensor dimensions.)

**Question 3:** Given the previous ResNet model and input image, compute the gradient of the top-1 output logit of the model with respect to the input image as done in Part I, Question 1.

**Question 4:** Perform Min-Max feature scaling on the RGB gradient from the previous step using `X_scaled = (X - X.min() ) / ( X.max() - X.min())`

**Question 5:** Visualize the scaled attribution using `plt.imshow()`.

# Part III: Guided-backpropagation

The goal of this section is to implement a variant of backpropagation known as guided-backpropagation. This approach focuses on modifying the gradient computation specifically for the ReLU activation function, rather than reimplementing the entire backpropagation algorithm from scratch. For additional details, please refer to lecture slide 232.

In [ ]:
# Load a pre-trained resnet model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# use device = xla.device() if you want to use tpu.
model = models.resnet18(pretrained=True).to(device)
# Set the model to evaluation mode
model.eval()

img_path = 'dog_tp4.jpg'
input_image = Image.open(img_path)

# preprocessing for ResNet
preprocess = transforms.Compose([
    transforms.Resize(256),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# set the ReLus to inplace = False
for i, (name, layer) in enumerate(model.named_modules()):
  if isinstance(layer, nn.ReLU):
    if name == "relu":
      getattr(model, name).inplace = False
    else:
      block, num, module = name.split(".")
      getattr(getattr(model,block)[int(num)], 'relu').inplace = False


# preprocess the image
input_tensor = preprocess(input_image)
# create a mini-batch as expected by the model
input_batch = input_tensor.unsqueeze(0)

################################################################################

**Question 1:** Complete the given code to implement guided-backpropagation as described in the lecture slide 232.
(Hint: Pay close attention to the tensor dimensions.)

In [ ]:
class reluGuidedBackprop(torch.autograd.Function):
    """
    We can implement our own custom autograd Functions by subclassing
    torch.autograd.Function and implementing the forward and backward passes
    which operate on Tensors.
    """
    def __init__(self, inplace=False):
      super(reluDeconv, self).__init__()
      self.inplace = inplace

    @staticmethod
    def forward(ctx, input):
        """
        In the forward pass we receive a Tensor containing the input and return
        a Tensor containing the output. ctx is a context object that can be used
        to stash information for backward computation. You can cache arbitrary
        objects for use in the backward pass using the ctx.save_for_backward method.
        """
        # ctx.save_for_backward(input)
        output = ???
        return output

    @staticmethod
    def backward(ctx, grad_output):
        """
        In the backward pass we receive a Tensor containing the gradient of the loss
        with respect to the output, and we need to compute the gradient of the loss
        with respect to the input.
        """
        grad_input = ???
        return grad_input

class reluGuidedBackpropWrapper(nn.Module):
    def __init__(self):
        super(reluGuidedBackpropWrapper, self).__init__()
    def forward(self, input):
        return reluGuidedBackprop.apply(input)

def replace_relu(model):
    for name, module in model.named_children():
        if isinstance(module, nn.ReLU):
            setattr(model, name, reluGuidedBackpropWrapper())
        else:
            replace_relu(module)

replace_relu(model)

**Question 2:** Given the previous ResNet model and input image, compute the gradient of the top-1 output logit of the model with respect to the input image as done in Part I, Question 1.

**Question 3:** Perform Min-Max feature scaling on the RGB gradient from the previous step using `X_scaled = (X - X.min() ) / ( X.max() - X.min())`

**Question 4:** Visualize the scaled attribution using `plt.imshow()`.

**Question 5:** Visualize all the implemented methods side by side.